# 機械学習モデルを作る！動かす！見てみる！

---
# このNotenbookの内容

- tf.kerasでオートエンコーダを作る
- VAEを作る
- 機械学習モデルを動かすプログラムを見てみる

***
# オートエンコーダを作る

- Wikipedia - オートエンコーダ  
[https://ja.wikipedia.org/wiki/オートエンコーダ](https://ja.wikipedia.org/wiki/%E3%82%AA%E3%83%BC%E3%83%88%E3%82%A8%E3%83%B3%E3%82%B3%E3%83%BC%E3%83%80)

In [ ]:
from keras.layers import Input, Dense
from keras.models import Model

'''
ここでは潜在変数について操作ができるよう、各層を作成してから層をつなげてネットワークを作成する。
エンコーダ入力層→（エンコーダ層）→出力（潜在変数）　と　デコーダ入力層（潜在変数）→（デコーダ層）→出力（＝入力）
input_img→encoded→（encoded_input→）decoded
を作成する。出力は層でないため作成不要。
'''

# 潜在変数の次元
encoding_dim = 36

# エンコーダ入力層
input_img = Input(shape=(784,), name='encoder_in')
# エンコーダ層
encoded = Dense(encoding_dim, activation='relu', name='encoder')(input_img)

# デコーダ入力層
encoded_input = Input(shape=(encoding_dim,), name='decoder_in')
# デコーダ層
decoded = Dense(784, activation='sigmoid', name='dencoder')(encoded)

# エンコーダとデコーダを一体化したモデル（オートエンコーダ全体）
autoencoder = Model(input_img, decoded)
# エンコーダのみのモデル
encoder = Model(input_img, encoded)
# オートエンコーダの最終層（decodeの層）
decoder_layer = autoencoder.layers[-1]
# デコーダのみのモデル
decoder = Model(encoded_input, decoder_layer(encoded_input))

# オートエンコーダのコンパイル、adadelta,二項交差エントロピー誤差
autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

#ネットワークの表示
autoencoder.summary()

In [ ]:
from keras.utils import plot_model
plot_model(
    autoencoder,
    show_shapes=True,
)

In [ ]:
# データセットの読み込み
from keras.datasets import mnist
from keras.utils import to_categorical
import numpy as np

#学習と評価にy_train、y_testは不要だが後で可視化するために格納。
(x_train, y_train), (x_test, y_test) = mnist.load_data()

#データの前処理
x_train = x_train.astype('float32') / 255.
x_test = x_test.astype('float32') / 255.
x_train = x_train.reshape((len(x_train), np.prod(x_train.shape[1:])))
x_test = x_test.reshape((len(x_test), np.prod(x_test.shape[1:])))

# 正解ラベルをone-hot-encoding
y_train = to_categorical(y_train, 10)
y_test = to_categorical(y_test, 10)

In [ ]:
# x_train -> x_trainのAE.
# テストデータもx_test -> x_testでよい。
autoencoder.fit(x_train, x_train,
                epochs=5,
                batch_size=100,
                shuffle=True,
                validation_data=(x_test, x_test))

In [ ]:
# 内在変数(encoded_ims)：テストデータのエンコード
# 内在変数による再構成データ(decoded_ims)：エンコードデータのデコード
encoded_imgs = encoder.predict(x_test)
decoded_imgs = decoder.predict(encoded_imgs)

In [ ]:
# matplotlibで描画
import matplotlib.pyplot as plt

#表示件数
n = 6
plt.figure(figsize=(10, 6))
for i in range(n):
    # 元データの表示
    ax = plt.subplot(3, n, i + 1)
    plt.imshow(x_test[i].reshape(28, 28))
    plt.gray()
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)

    # 中間データの表示
    ax = plt.subplot(3, n, i + 1 + n)
    plt.imshow(encoded_imgs[i].reshape(6, 6))
    plt.gray()
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)

    # 再構成データの表示
    ax = plt.subplot(3, n, i + 1 + 2*n)
    plt.imshow(decoded_imgs[i].reshape(28, 28))
    plt.gray()
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)

plt.show()

***
# ラベル判別をする機械学習モデル

In [ ]:
from keras.layers import Input, Dense
from keras.models import Model

'''
最終層をsoftmax関数10次元にする
'''

mid_dim = 36
out_dim = 10

input_img = Input(shape=(784,), name='classifier_in')
classifier_mid = Dense(mid_dim, activation='relu', name='classifier_mid')(input_img)
classifier_out = Dense(out_dim, activation='softmax', name='classifier_out')(classifier_mid)

classifier = Model(input_img, classifier_out)

classifier.compile(optimizer='adam', loss='categorical_crossentropy',metrics=['accuracy'])
classifier.summary()

In [ ]:
# データセットの読み込み
from keras.datasets import mnist
from keras.utils import to_categorical
import numpy as np

#学習と評価にy_train、y_testは不要だが後で可視化するために格納。
(x_train, y_train), (x_test, y_test) = mnist.load_data()

#データの前処理
x_train = x_train.astype('float32') / 255.
x_test = x_test.astype('float32') / 255.
x_train = x_train.reshape((len(x_train), np.prod(x_train.shape[1:])))
x_test = x_test.reshape((len(x_test), np.prod(x_test.shape[1:])))

# 正解ラベルをone-hot-encoding
y_train = to_categorical(y_train, 10)
y_test = to_categorical(y_test, 10)

In [ ]:
classifier.fit(
    x_train, y_train,
    epochs=5,
    batch_size=64,
    shuffle=True,
    validation_data=(x_test, y_test)
)

ここまでのコードで `classifier` は MNIST手書き文字データセットのone-hotラベルを学習しました。  
生成ＡＩに可視化のプログラムを作ってもらい、結果を可視化してみましょう。

<details><summary>コード作成例（クリックで表示）</summary>

```python  
import numpy as np
import matplotlib.pyplot as plt

# --- テストデータで予測 ---
y_pred = classifier.predict(x_test)
y_pred_classes = np.argmax(y_pred, axis=1)

# one-hot で学習している場合は y_test も one-hot → 整数に戻す
if y_test.ndim > 1:
    y_true = np.argmax(y_test, axis=1)
else:
    y_true = y_test

# --- 最初の 25 枚を可視化 ---
plt.figure(figsize=(10, 10))
for i in range(25):
    plt.subplot(5, 5, i + 1)
    plt.imshow(x_test[i].reshape(28, 28), cmap="gray")
    plt.axis("off")
    plt.title(f"T:{y_true[i]}, P:{y_pred_classes[i]}")  # T=正解, P=予測
plt.tight_layout()
plt.show()
```
</details>


In [ ]:
# 生成ＡＩに分類結果を可視化してもらう
import numpy as np
import matplotlib.pyplot as plt

# --- テストデータで予測 ---
y_pred = classifier.predict(x_test)
y_pred_classes = np.argmax(y_pred, axis=1)

# one-hot で学習している場合は y_test も one-hot → 整数に戻す
if y_test.ndim > 1:
    y_true = np.argmax(y_test, axis=1)
else:
    y_true = y_test

# --- 最初の 25 枚を可視化 ---
plt.figure(figsize=(10, 10))
for i in range(25):
    plt.subplot(5, 5, i + 1)
    plt.imshow(x_test[i].reshape(28, 28), cmap="gray")
    plt.axis("off")
    plt.title(f"T:{y_true[i]}, P:{y_pred_classes[i]}")  # T=正解, P=予測
plt.tight_layout()
plt.show()


***
# VAEを作る

In [ ]:
# ===== Keras 3 + TF 2.18 で動く最小 VAE =====
# 依存: pip install "keras>=3.4" "tensorflow>=2.18"

import tensorflow as tf
import keras
from keras import layers, ops, random
from keras.datasets import mnist

print("keras:", keras.__version__, "backend:", keras.backend.backend())
print("tf:", tf.__version__)

# ----- 1) Data -----
# (x_train, _), (x_test, _) = mnist.load_data()
# x_train = (x_train.astype("float32") / 255.).reshape((len(x_train), -1))
# x_test  = (x_test.astype("float32") / 255.).reshape((len(x_test), -1))

original_dim = x_train.shape[1]   # 784
intermediate_dim = 500
latent_dim = 2
batch_size = 128
epochs = 1  # 動作確認用に 1

# ----- 2) Sampling Layer -----
class Sampling(layers.Layer):
    def call(self, inputs):
        z_mean, z_log_var = inputs
        batch = ops.shape(z_mean)[0]
        dim = z_mean.shape[-1]
        eps = random.normal(shape=(batch, dim))
        return z_mean + ops.exp(0.5 * z_log_var) * eps

# ----- 3) Encoder -----
x_in = layers.Input(shape=(original_dim,))
h = layers.Dense(intermediate_dim, activation="relu")(x_in)
z_mean = layers.Dense(latent_dim, name="z_mean")(h)
z_log_var = layers.Dense(latent_dim, name="z_log_var")(h)
z = Sampling()([z_mean, z_log_var])
encoder = keras.Model(x_in, [z_mean, z_log_var, z], name="encoder")

# ----- 4) Decoder -----
z_in = layers.Input(shape=(latent_dim,))
dh = layers.Dense(intermediate_dim, activation="relu")(z_in)
y_out = layers.Dense(original_dim, activation="sigmoid")(dh)
decoder = keras.Model(z_in, y_out, name="decoder")

# ----- 5) VAE Model -----
class VAE(keras.Model):
    def __init__(self, encoder, decoder, original_dim):
        super().__init__(name="vae")
        self.encoder = encoder
        self.decoder = decoder
        self.original_dim = original_dim

    def call(self, x, training=False):
        _, _, z = self.encoder(x, training=training)
        return self.decoder(z, training=training)

    def compute_total_loss(self, x, training):
        z_mean, z_log_var, z = self.encoder(x, training=training)
        y_pred = self.decoder(z, training=training)

        eps = 1e-7
        # BCE per sample
        recon_per_elem = -(x * ops.log(y_pred + eps) +
                           (1.0 - x) * ops.log(1.0 - y_pred + eps))
        recon_loss = ops.sum(recon_per_elem, axis=-1)

        # KL per sample
        kl = 1 + z_log_var - ops.square(z_mean) - ops.exp(z_log_var)
        kl = -0.5 * ops.sum(kl, axis=-1)

        total = ops.mean(recon_loss + kl)
        return total, recon_loss, kl

    def train_step(self, data):
        x = data[0] if isinstance(data, (tuple, list)) else data
        with tf.GradientTape() as tape:  # ← keras ではなく tf
            total, recon_loss, kl = self.compute_total_loss(x, training=True)
        grads = tape.gradient(total, self.trainable_weights)
        self.optimizer.apply_gradients(zip(grads, self.trainable_weights))
        return {"loss": total,
                "recon": ops.mean(recon_loss),
                "kl": ops.mean(kl)}

    def test_step(self, data):
        x = data[0] if isinstance(data, (tuple, list)) else data
        total, recon_loss, kl = self.compute_total_loss(x, training=False)
        return {"loss": total,
                "recon": ops.mean(recon_loss),
                "kl": ops.mean(kl)}

vae = VAE(encoder, decoder, original_dim)
vae.compile(optimizer=keras.optimizers.Adam())

# summary
vae.build((None, original_dim))
vae.summary()
encoder.summary()
decoder.summary()

# ----- 6) Train -----
# vae.fit(x_train, epochs=epochs, batch_size=batch_size,
#         validation_data=(x_test, None))

# ----- 7) Generate samples -----
# import numpy as np
# z_samples = np.random.normal(size=(16, latent_dim)).astype("float32")
# x_gen = decoder.predict(z_samples, verbose=0)
# print("Generated batch shape:", x_gen.shape)


***
生成ＡＩに↑のコードを一行ずつ解説してもらてみてください。
***

In [ ]:
from tensorflow.keras.utils import plot_model
plot_model(encoder,show_shapes=True)

In [ ]:
plot_model(decoder,show_shapes=True)


In [ ]:
# データセットの読み込み
from tensorflow.keras.datasets import mnist
from tensorflow.keras.utils import to_categorical
import numpy as np

#学習と評価にy_train、y_testは不要だが後で可視化するために格納。
(x_train, y_train), (x_test, y_test) = mnist.load_data()

#データの前処理
x_train = x_train.astype('float32') / 255.
x_test = x_test.astype('float32') / 255.
x_train = x_train.reshape((len(x_train), np.prod(x_train.shape[1:])))
x_test = x_test.reshape((len(x_test), np.prod(x_test.shape[1:])))

# 正解ラベルをone-hot-encoding
y_train = to_categorical(y_train, 10)
y_test = to_categorical(y_test, 10)

epochs=10 # エポック数
batch_size= 100 # バッチサイズ
vae.fit(x_train,
        shuffle=True,
        epochs=epochs,
        batch_size=batch_size*5,
        validation_data=(x_test, None))

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt

# 内在変数(encoded_zvals)：テストデータのエンコード
# 内在変数による再構成データ(decoded_ims)：エンコードデータのデコード
encoded_zvals = encoder.predict(x_test, batch_size=batch_size)
decoded_imgs = decoder.predict(encoded_zvals[2])

# 各ラベルの中心の取得
z_means=[]
for i in range(10):
  x_i = x_train[np.argmax(y_train, axis=1)==i]
  x_i_zvals = encoder.predict(x_i, batch_size=batch_size)
  z_means.append(np.mean(x_i_zvals[0], axis=0))

#内在変数の平均の散布図
plt.figure(figsize=(8, 6))
plt.scatter(encoded_zvals[0][:, 0], encoded_zvals[0][:, 1], c=np.argmax(y_test, axis=1), cmap='tab10', linewidths=0.1, marker='.')
plt.colorbar()
for test in range(6):
    plt.scatter(encoded_zvals[0][test, 0], encoded_zvals[0][test, 1], color='r', marker='o', linewidths=5)
    plt.scatter(encoded_zvals[0][test, 0], encoded_zvals[0][test, 1], color='white', marker='$'+str(np.argmax(y_test[test]))+'$')
plt.show()

In [ ]:
# ベクトル空間から手書き文字画像を生成するAI(?)
point = np.array([[2,-4]]) # ここに適当な座標を入力
decoded_point = decoder.predict(point)

plt.imshow(decoded_point.reshape(28, 28))
plt.gray()

plt.show() 

In [ ]:
#ある点からある点への変遷表示
n = 21
plt.figure(figsize=(21, 4))

#両端の座標
left_side = np.array([-4,0])
right_side = np.array([4,0])

#テストデータ
convex_hull = np.vstack((np.linspace(left_side[0],right_side[0],n), np.linspace(left_side[1],right_side[1],n)))
convex_hull = np.transpose(convex_hull)
decoded_convex_hull = decoder.predict(convex_hull)

for i in range(n):
    # 再構成データの表示
    ax = plt.subplot(1, n, i + 1)
    plt.imshow(decoded_convex_hull[i].reshape(28, 28))
    plt.gray()
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)

plt.show()

上のコードを修正して、座標`[0,-4]`から座標`[0,4]`までの画像を生成してみてください。

In [ ]:
# 試しに数字文字列を生成してみる。
input_str = '20250903' #数字文字列
log_var = 0.05 #サンプリングの分散
n = len(input_str)
input_means = np.array([z_means[int(j)] for j in input_str])

input_decoded = decoder.predict(input_means+log_var*np.random.normal(size=input_means.shape))

plt.figure(figsize=(n,5))
for i in range(n):
    # 再構成データの表示
    ax = plt.subplot(1, n, i + 1)
    plt.imshow(input_decoded[i].reshape(28, 28))
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)

plt.subplots_adjust(wspace=-0.1)
plt.show()

***
# 機械学習モデルを動かすプログラムを見てみる

### Hugging Face とは

AI研究・開発のためのオープンプラットフォームを提供するコミュニティサイト。

大規模データセットや学習済みモデル、Webアプリの公開ができます。

### Transformers とは

Hugging Face が開発している Pythonライブラリ。
Transformer系のモデルアーキテクチャ（BERT, GPTなど）を簡単に使える統一APIを提供しています。

Hugging face Hub に公開されたモデルを簡単にロードして利用できる。

## オープンウェイトモデル

オープンライセンスのもとで公開されている機械学習モデルのことを指します。  
モデルは「アーキテクチャ（ネットワークの構造）」と「学習済みの重みパラメータ（weights）」から成り立っており、
特に後者を公開することが「オープンウェイト」と呼ばれます。

- Google - BERT model(2019)  
  [https://huggingface.co/google-bert/bert-base-uncased](https://huggingface.co/google-bert/bert-base-uncased)

- OpenAI - gpt-2 model(2019)  
  [https://huggingface.co/openai-community/gpt2](https://huggingface.co/openai-community/gpt2)

- OpenAI 「gpt-ossが登場」  
  [https://openai.com/ja-JP/index/introducing-gpt-oss/](https://openai.com/ja-JP/index/introducing-gpt-oss/)